In [1]:
from dnd.monsters.circus_fighter import create_warrior
from dnd.entity import Entity
from dnd.blocks.equipment import WeaponSlot
from dnd.core.dice import Dice, RollType, AttackOutcome
from uuid import uuid4
from dnd.core.events import EventQueue

import time
from uuid import UUID



In [2]:
start_time = time.time()
source_id = uuid4()
proficiency_bonus = 2

In [3]:
q = EventQueue()

In [4]:
warrior = create_warrior(source_id,proficiency_bonus,position=(0,0))
# q._all_events


In [5]:
warrior2 = create_warrior(name="Mona",position=(1,1))
# q._all_events


In [6]:
from dnd.core.events import Event, EventType, EventPhase
from typing import Optional
from dnd.core.base_tiles import floor_factory

In [7]:
flor_00 = floor_factory((0,0))
flor_01 = floor_factory((0,1))
flor_10 = floor_factory((1,0))
flor_11 = floor_factory((1,1))


In [8]:
from dnd.actions import Attack, AttackEvent, Movement, MovementEvent
weapon_slot = WeaponSlot.MAIN_HAND

In [9]:
Entity.update_all_entities_senses()


paths before filtering: {(0, 0): [(0, 0)], (0, 1): [(0, 0), (0, 1)], (1, 0): [(0, 0), (1, 0)], (1, 1): [(0, 0), (1, 1)]}
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}


In [10]:
attack = Attack(name="Warrior Main Hand attack",
                source_entity_uuid=warrior.uuid,
                target_entity_uuid=warrior2.uuid,
                weapon_slot= WeaponSlot.MAIN_HAND)
                
attack2=Attack(name="Warrior2 Main Hand attack",
               source_entity_uuid=warrior2.uuid,
               target_entity_uuid=warrior.uuid,
               weapon_slot= WeaponSlot.MAIN_HAND)


In [11]:
Entity.update_all_entities_senses()

print(warrior.senses.paths)

paths before filtering: {(0, 0): [(0, 0)], (0, 1): [(0, 0), (0, 1)], (1, 0): [(0, 0), (1, 0)], (1, 1): [(0, 0), (1, 1)]}
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}
defaultdict(<class 'list'>, {(0, 0): [(0, 0)], (0, 1): [(0, 0), (0, 1)], (1, 0): [(0, 0), (1, 0)], (1, 1): [(0, 0), (1, 1)]})


In [12]:
movement = Movement(name="Warrior Movement",
                    source_entity_uuid=warrior.uuid,
                    end_position=(1,1))


In [13]:
movement.costs

[Cost(name='Movement Cost', cost_type='movement', cost=2, evaluator=<function entity_action_economy_cost_evaluator at 0x00000293375194E0>)]

In [14]:
start_time = time.time()



In [15]:
start_time = time.time()

movement.pre_validate()
print(time.time()-start_time)


pre-validation successful
0.0004999637603759766


In [16]:
print(warrior.position)
start_time = time.time()
movement.apply()
print(time.time()-start_time)


(0, 0)
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}
paths before filtering: {(1, 1): [(1, 1)], (1, 0): [(1, 1), (1, 0)], (0, 1): [(1, 1), (0, 1)], (0, 0): [(1, 1), (0, 0)]}
0.0010001659393310547


In [17]:
print(warrior.position)


(1, 1)


In [18]:
from dnd.core.events import Trigger, EventHandler, EventProcessor

In [19]:
attack_trigger = Trigger(name="Attack Trigger",
                         event_type=EventType.ATTACK,
                         event_phase=EventPhase.DECLARATION)



def attack_processor(event: AttackEvent, source_entity_uuid: UUID ) -> Optional[AttackEvent]:
    print(f"Simple Attack event received for {source_entity_uuid} with target {event.target_entity_uuid} in phase {event.phase}")
    return event

def precise_attack_processor(event: AttackEvent, source_entity_uuid: UUID ) -> Optional[AttackEvent]:
    print(f"Precise attack event received for {source_entity_uuid} with target {event.target_entity_uuid} in phase {event.phase}")
    return event

test_handler = EventHandler(name="Test Handler",
                            trigger_conditions=[attack_trigger],
                            event_processor=attack_processor,
                            source_entity_uuid=warrior2.uuid)



precise_attack_trigger = Trigger(name="Attack Trigger",
                         event_type=EventType.ATTACK,
                         event_phase=EventPhase.DECLARATION,
                         event_source_entity_uuid=warrior.uuid,
                         event_target_entity_uuid=warrior2.uuid)
test_precise_handler = EventHandler(name="Test Precise Handler",
                                    trigger_conditions=[precise_attack_trigger],
                                    event_processor=precise_attack_processor,
                                    source_entity_uuid=warrior2.uuid)



In [20]:
test_handler.trigger_conditions[0].is_simple()

True

In [21]:
warrior2.add_event_handler(test_handler)
warrior2.add_event_handler(test_precise_handler)

In [22]:
warrior2.get_hp()

58

In [23]:
# Trigger condition: event_type=<EventType.ATTACK: 'attack'> event_phase=<EventPhase.DECLARATION: 'declaration'> event_source_entity_uuid=UUID('7f40519e-37ae-411d-81e9-90fafbccdd92') event_target_entity_uuid=UUID('9ec24cff-1dc5-4af7-a768-db9962dea6ea')


In [24]:
#measure time of attack
start_time = time.time()
attack.apply()
attack_time = time.time()-start_time
print(f"Attack time: {attack_time}")

Simple Attack event received for a7578046-2336-4d94-b6d0-6284d56359b5 with target a7578046-2336-4d94-b6d0-6284d56359b5 in phase EventPhase.DECLARATION
Precise attack event received for a7578046-2336-4d94-b6d0-6284d56359b5 with target a7578046-2336-4d94-b6d0-6284d56359b5 in phase EventPhase.DECLARATION
Simple Attack event received for a7578046-2336-4d94-b6d0-6284d56359b5 with target a7578046-2336-4d94-b6d0-6284d56359b5 in phase EventPhase.DECLARATION
Precise attack event received for a7578046-2336-4d94-b6d0-6284d56359b5 with target a7578046-2336-4d94-b6d0-6284d56359b5 in phase EventPhase.DECLARATION
Simple Attack event received for a7578046-2336-4d94-b6d0-6284d56359b5 with target a7578046-2336-4d94-b6d0-6284d56359b5 in phase EventPhase.DECLARATION
Precise attack event received for a7578046-2336-4d94-b6d0-6284d56359b5 with target a7578046-2336-4d94-b6d0-6284d56359b5 in phase EventPhase.DECLARATION
Attack time: 0.008997201919555664


In [25]:
warrior2.remove_event_handler(test_handler)

In [26]:
attack2.apply()

AttackEvent(name='Warrior2 Main Hand attack', uuid=UUID('bffb20c1-c39e-4f4c-b52e-7486726be5d6'), source_entity_uuid=UUID('a7578046-2336-4d94-b6d0-6284d56359b5'), source_entity_name=None, target_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), target_entity_name=None, context=None, use_register=True, lineage_uuid=UUID('d2afcc4a-da5c-4aab-9e5e-683da2400b6d'), timestamp=datetime.datetime(2025, 5, 17, 18, 13, 54, 852602), event_type=<EventType.ATTACK: 'attack'>, phase=<EventPhase.COMPLETION: 'completion'>, modified=True, canceled=False, parent_event=None, status_message='Attack missed', lineage_children_events=[], children_events=[], costs=[Cost(name='Attack Cost', cost_type='actions', cost=1, evaluator=<function entity_action_economy_cost_evaluator at 0x00000293375194E0>)], weapon_slot=<WeaponSlot.MAIN_HAND: 'MAIN_HAND'>, range=Range(type=<RangeType.REACH: 'Reach'>, normal=5, long=None), attack_bonus=ModifiableValue(name='Value_Attack Bonus_Attack Bonus_Melee Attack Bonus_strengt

In [27]:
warrior.get_damages(weapon_slot=WeaponSlot.MAIN_HAND,target_entity_uuid=warrior.uuid)

[Damage(name='Damage', uuid=UUID('e5ff1471-c34a-46f3-821b-b44ca1b75778'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, use_register=True, damage_dice=6, dice_numbers=1, damage_bonus=ModifiableValue(name='Damage Bonus_strength Ability Score_strength Modifier Bonus_Melee Damage Bonus_Damage Bonus', uuid=UUID('3405ed5f-e22a-480e-bd0e-2c73e0e8ccc6'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), target_entity_name=None, context=None, use_register=True, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x000002933735E840>, generated_from=[UUID('295e723d-eb1b-4e18-bac9-5cd13c3591cd'), UUID('77e6a20b-f5ff-4d9b-9446-65fe89b853db'), UUID('594d1246-828b-4486-95c9-7b6de0192c6b'), UUID('295e723d-eb1b-4e18-bac9-5cd13c3591cd')], global_normalizer=False, self_static

In [28]:
for event in q._all_events:
    print(event.name,event.status_message)


Performer's Leather Armor None
Performer's Leather Armor None
Performer's Leather Armor None
Performer's Leather Armor None
Flaming Scimitar None
Flaming Scimitar None
Flaming Scimitar None
Flaming Scimitar None
Rusty Dagger None
Rusty Dagger None
Rusty Dagger None
Rusty Dagger None
Dual Wielder None
Dual Wielder Applied Dual Wielder contextual ac modifer condition to Ganger
Dual Wielder Applied Dual Wielder contextual ac modifer condition to Ganger
Elemental Weapon Mastery None
Elemental Weapon Mastery Applied Elemental Weapon Mastery contextual advantage modifier condition to Ganger
Elemental Weapon Mastery Applied Elemental Weapon Mastery contextual advantage modifier condition to Ganger
Elemental Affinity None
Elemental Affinity Applied Elemental Affinity resistance modifier condition to Ganger
Elemental Affinity Applied Elemental Affinity resistance modifier condition to Ganger
Circus Performer None
Circus Performer Applied Circus Performer condition to Ganger
Circus Performer App

In [29]:
warrior2.get_hp()

53

In [30]:
warrior.action_economy.actions.normalized_score

0

In [31]:
warrior.action_economy.actions.self_static.value_modifiers

{UUID('95e4f1cf-2c5f-4ba1-a8ef-989ff1ea191d'): NumericalModifier(name='Actions_base_value', uuid=UUID('95e4f1cf-2c5f-4ba1-a8ef-989ff1ea191d'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), target_entity_name=None, context=None, use_register=True, value=1, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x000002933735F240>, normalized_value=1),
 UUID('0e242319-c7c2-4533-9098-cb1b2369e2cd'): NumericalModifier(name='cost', uuid=UUID('0e242319-c7c2-4533-9098-cb1b2369e2cd'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, use_register=True, value=-1, score_normalizer=None, normalized_value=-1)}

In [32]:
warrior.action_economy.reset_all_costs()

In [33]:
warrior.action_economy.actions.normalized_score

1

In [34]:
warrior.source_entity_uuid

UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a')

In [35]:
warrior.ability_scores.uuid


UUID('1aaaed50-3120-4feb-892d-9c0b309cfdd0')

In [36]:
Entity.get(warrior.source_entity_uuid)

Entity(name='Ganger', description='A level 4 fighter character with a past in the circus and spiked claws for hands.', uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={UUID('1aaaed50-3120-4feb-892d-9c0b309cfdd0'): AbilityScores(name='ability_scores', description=None, uuid=UUID('1aaaed50-3120-4feb-892d-9c0b309cfdd0'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={UUID('1f6cbad3-93fd-497e-be91-5f5b89eb677f'): Ability(name='strength', description=None, uuid=UUID('1f6cbad3-93fd-497e-be91-5f5b89eb677f'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, blocks={}, values={UUID('dcaa3607-bbd4-4874-87a3-7620f4eab49

In [37]:
from dnd.conditions import Paralyzed

In [38]:
paralyzed_condition = Paralyzed(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)
paralyzed_condition.apply()


ConditionApplicationEvent(name='Paralyzed', uuid=UUID('e3931574-2bc2-418f-8788-bde0a777366b'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=UUID('a7578046-2336-4d94-b6d0-6284d56359b5'), target_entity_name=None, context=None, use_register=True, lineage_uuid=UUID('d71bbe8e-f950-45c0-ae65-910f77c6021e'), timestamp=datetime.datetime(2025, 5, 17, 18, 13, 55, 160969), event_type=<EventType.CONDITION_APPLICATION: 'condition_application'>, phase=<EventPhase.COMPLETION: 'completion'>, modified=True, canceled=False, parent_event=None, status_message='Applied Paralyzed to target contextual critical modifier to Mona', lineage_children_events=[UUID('5756b9bd-0149-4a16-bee4-d29cf72c2dbc'), UUID('4ebd74d0-a115-46db-a838-c6d23bf23f9e'), UUID('145edb66-eef3-44f1-a991-0b61f1049fad'), UUID('05ac3db3-904b-4bcc-8649-b073e459fbf4'), UUID('786bc89d-a87e-4d7e-9f05-73fc69741b47'), UUID('5eb1614a-e932-4e76-8a81-85f59092571e'), UUID('5756b9bd-0149-4

In [39]:
weapon_slot = WeaponSlot.MAIN_HAND

warrior_bonus = warrior.attack_bonus(target_entity_uuid=warrior2.source_entity_uuid,weapon_slot=weapon_slot)

In [ ]:
warrior.ability_scores.get_ability("strength").ability_score.normalized_score+warrior.ability_scores.get_ability("strength").modifier_bonus.normalized_score



4

In [41]:
warrior_bonus.normalized_score

5

In [42]:
attack_dice = Dice(count=1,value=20,bonus=warrior_bonus, roll_type=RollType.ATTACK)
attack_roll = attack_dice.roll
print(f"Attack roll result: {attack_roll.total}")








Attack roll result: 14


In [43]:
attack_roll.bonus

5

In [44]:
attack_roll.results

9

In [45]:
import time

In [46]:
start_time = time.time()
damages = warrior.get_damages(weapon_slot)
print(time.time()-start_time)

0.0005037784576416016


In [47]:
start_time = time.time()
attack_bonus = warrior.attack_bonus(weapon_slot= weapon_slot)
print(time.time()-start_time)


0.0004999637603759766


In [48]:
start_time = time.time()
ac = warrior2.ac_bonus()
print(time.time()-start_time)
start_time = time.time()

0.0005021095275878906


In [49]:
damages

[Damage(name='Damage', uuid=UUID('bfdab1ac-fc2e-430c-aa17-969e16c025d9'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, use_register=True, damage_dice=6, dice_numbers=1, damage_bonus=ModifiableValue(name='Damage Bonus_strength Ability Score_strength Modifier Bonus_Melee Damage Bonus_Damage Bonus', uuid=UUID('2e1075d3-e187-4d0d-aab4-3f1e915e0d67'), source_entity_uuid=UUID('9ac7e9d7-c634-4123-ab72-5e14b245453a'), source_entity_name=None, target_entity_uuid=None, target_entity_name=None, context=None, use_register=True, score_normalizer=<function ModifiableValue.create.<locals>.<lambda> at 0x000002933735E840>, generated_from=[UUID('295e723d-eb1b-4e18-bac9-5cd13c3591cd'), UUID('504324db-ed6f-4b29-8e6f-93f283d3d8b3'), UUID('594d1246-828b-4486-95c9-7b6de0192c6b'), UUID('295e723d-eb1b-4e18-bac9-5cd13c3591cd')], global_normalizer=False, self_static=StaticValue(name='A Value_A Value_A Val

In [50]:
start_time = time.time()
warrior.set_target_entity(warrior2.uuid)
print(time.time()-start_time)

0.0015006065368652344


In [51]:
warrior.target_entity_uuid=warrior2.uuid

In [52]:
a = warrior.uuid

In [53]:
start_time = time.time()
warrior2.target_entity_name="warrior.uuid"
print(time.time()-start_time)

0.0004990100860595703


In [54]:
start_time = time.time()
warrior2.target_entity_uuid=warrior.uuid
print(time.time()-start_time)

0.0


In [55]:
start_time = time.time()
warrior2.set_target_entity(warrior.uuid)
print(time.time()-start_time)

0.0014984607696533203


In [56]:
start_time = time.time()
warrior2.set_target_entity(warrior.uuid)
print(time.time()-start_time)

0.0015070438385009766


In [57]:
start_time = time.time()
warrior.attack(warrior2.uuid,weapon_slot)
print(time.time()-start_time)


AttributeError: 'Entity' object has no attribute 'attack'

In [28]:
warrior_strenght_modifer = warrior.ability_scores.get_ability("strength").get_combined_values()
warrior_ac = warrior.ac_bonus()

In [ ]:
acrobatics_skill_request = warrior.create_skill_check_request(warrior2.uuid, "acrobatics",warrior_ac.uuid)
perception_skill_request = warrior.create_skill_check_request(warrior2.uuid, "perception",warrior_ac.uuid)
strength_saving_throw_request = warrior.create_saving_throw_request(warrior2.uuid, "strength",warrior_ac.uuid)

In [ ]:
acrobatics_skill_request

In [ ]:
strength_saving_throw_request

In [ ]:
warrior2.skill_bonus(warrior.uuid,skill_name="acrobatics")

In [ ]:
warrior2.skill_check(acrobatics_skill_request)

In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
warrior2.saving_throw_bonus(warrior.uuid, "strength")

In [ ]:
warrior2.saving_throw(strength_saving_throw_request)


In [ ]:
from dnd.conditions import Blinded
from dnd.core.events import EventQueue


blinded = Blinded(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)
blinded.apply()



In [ ]:

warrior2.equipment.attack_bonus.advantage


In [ ]:
warrior.equipment.attack_bonus.advantage


In [ ]:
blinded.modifers_uuids

In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
blinded.remove()


In [ ]:
warrior2.skill_check(perception_skill_request)

In [ ]:
warrior2.equipment.attack_bonus.advantage


In [48]:
from dnd.core.modifiers import ContextualNumericalModifier, NumericalModifier, ContextAwareNumerical
from typing import Optional, Dict, Any
from uuid import UUID


In [49]:
from dnd.conditions import Charmed

charmed = Charmed(source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid)


In [ ]:
charmed.apply()


In [ ]:
deception_skill_request = warrior2.create_skill_check_request(warrior.uuid, "deception",15)

warrior.skill_check(deception_skill_request)





In [53]:
def hate_mona(source_entity_uuid: UUID, target_entity_uuid: Optional[UUID]=None, context: Optional[Dict[str, Any]]=None) -> NumericalModifier:
    """ function that cheks if the target name is Mona, in that case it gives a +5 modifier"""
    if target_entity_uuid is not None:
        target_entity = Entity.get(target_entity_uuid)
    else:
        target_entity = None
    if isinstance(target_entity, Entity) and target_entity.name == "Mona":
        return NumericalModifier(source_entity_uuid=source_entity_uuid, target_entity_uuid=target_entity_uuid, value=5)
    else:
        return NumericalModifier(source_entity_uuid=source_entity_uuid, target_entity_uuid=target_entity_uuid, value=0)

hate_mona_modifier = ContextualNumericalModifier(name="Hate Mona",source_entity_uuid=warrior.uuid, target_entity_uuid=warrior2.uuid, callable=hate_mona)


In [ ]:
warrior.equipment.attack_bonus.self_contextual.add_value_modifier(hate_mona_modifier)


In [ ]:
warrior.set_target_entity(warrior2.uuid)
warrior.equipment.attack_bonus.normalized_score


In [ ]:
warrior.clear_target_entity()
warrior.equipment.attack_bonus.normalized_score


In [57]:
warrior.senses.entities[warrior2.uuid]=(1,0)

In [ ]:
from dnd.conditions import Frightened
frightened = Frightened(source_entity_uuid=warrior2.uuid, target_entity_uuid=warrior.uuid)
frightened.apply()






In [ ]:
warrior.action_economy.movement.normalized_score


In [ ]:
warrior.senses.entities = {}
warrior.action_economy.movement.normalized_score


In [ ]:
print(f"total_time: {time.time()-start_time}")